In [1]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys

from selenium.webdriver.chrome.service import Service
# Initialize the WebDriver
import pickle
import csv
import time
from datetime import datetime
from selenium import webdriver

from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from webdriver_manager.chrome import ChromeDriverManager
from selenium.common.exceptions import NoSuchElementException


In [2]:
#!pip install translate
#!pip install --user -U nltk
#! pip install googletrans
import nltk
nltk.download('vader_lexicon')
from googletrans import Translator
from nltk.sentiment import SentimentIntensityAnalyzer
from tqdm.notebook import tqdm


[nltk_data] Downloading package vader_lexicon to
[nltk_data]     C:\Users\Admin\AppData\Roaming\nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


In [50]:
chromedriver_path = "chromedriver-win64\chromedriver.exe"
service = Service(chromedriver_path)

# Initialize the WebDriver with the Service object



In [51]:
driver = webdriver.Chrome(service=service)

driver.get('https://www.facebook.com/')
cookies = pickle.load(open("my_cookie.pkl","rb"))
for cookie in cookies:
    driver.add_cookie(cookie)

# 3. Refresh the browser
driver.get('https://www.facebook.com/')




## Supported Functions to handle web data

In [52]:
import time
from collections import defaultdict
from datetime import datetime
import locale
import time
from datetime import datetime, timedelta
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as ECd
def split_at_first_space(input_str):
    first_part, second_part = input_str.split(' ', 1)
    return first_part, second_part  
def parse_facebook_date(date_text):
    """
    Parse the date and time from Facebook post date text.
    Handles both absolute dates (e.g., "January 17, 2024 at 12:00 PM")
    and relative dates (e.g., "3 hours ago").
    """
    # Check if the input contains " at " to determine the format
    if ' at ' in date_text:
        # Split date_text into date part and time part
        date_part, time_part = date_text.split(' at ')
        
        # Parse the date part
        try:
            post_datetime = datetime.strptime(date_part, '%d %B %Y')
        except ValueError:
            raise ValueError("Date format '{}' does not match expected absolute format.".format(date_text))
        
        # Parse the time part and combine with date
        try:
            time_obj = datetime.strptime(time_part, '%H:%M')
            post_datetime = post_datetime.replace(hour=time_obj.hour, minute=time_obj.minute)
        except ValueError:
            raise ValueError("Time format '{}' does not match expected absolute format.".format(date_text))
        
    else:
        # Handle relative dates (not implemented in this example)
        raise NotImplementedError("Relative dates parsing is not implemented.")
    
    return post_datetime
def parse_share_count(share_text):
    """
    Parse the share count text and convert it to an integer.
    Handles formats like '1.2K' and returns 1200.
    """
    count, sub = split_at_first_space(share_text)
    final_share_count = count.strip().upper()
    if 'K' in final_share_count:
        return int(float(final_share_count.replace('K', '')) * 1000)
    elif 'M' in final_share_count:
        return int(float(final_share_count.replace('M', '')) * 1000000)
    else:
        return int(final_share_count)
def reaction_count(react):
    final_share_count = react.upper()
    if 'K' in final_share_count:
        return int(float(final_share_count.replace('K', '')) * 1000)
    elif 'M' in final_share_count:
        return int(float(final_share_count.replace('M', '')) * 1000000)
    else:
        return int(final_share_count)

    
        



2300
<class 'int'>


## Get permalink of recent posts

In [62]:


page_ur = 'https://www.facebook.com/MTP.Fan/'  # Update this to the target page URL

def get_post_link(page_url):
    # Open the page
    driver.get(page_url)
    time.sleep(5)  # Adjust sleep time as needed for the page to fully load

    n_scrolls = 20
    post_links = set()  # Use a set to avoid duplicates

    while len(list(post_links)) < 200:
        # Scroll down the page in smaller increments

        driver.execute_script("window.scrollBy(0, window.innerHeight);")
        time.sleep(0.2)

        # Find post links, which typically contain "/posts/" or "/permalink/"
        anchors = driver.find_elements(By.TAG_NAME, 'a')
        anchors = [a.get_attribute('href') for a in anchors if a.get_attribute('href')]
        
        # Filter out the links that contain '/posts/' or '/permalink/'
        new_post_links = [a for a in anchors if '/posts/' in a or '/permalink/' in a]
        

        
        # Add new links to the set to avoid duplicates
        post_links.update(new_post_links)
        print(len(post_links))
        # Wait for new content to load after scrolling



    # Print the post links, ensuring we only print the first 10
    for i, permalink in enumerate(post_links, start=1):
        print(f'Post {i}: {permalink}')
        
    return list(post_links)

## Extract Post Data using inspect elements

In [128]:
from selenium.common.exceptions import NoSuchElementException

def extract_post_data(post_links,starts):
    data = []
    for i, post_link in enumerate(post_links, start=1):
        driver.get(post_link)
        time.sleep(5)  # Adjust sleep time as needed for the post to load
        post_data = {'post_id': i + starts}
        print(i)
        # Extract caption
        try:
            # Find the div element containing images from the main post
            try:
                main_post_div = driver.find_element(By.ID, ':R5al5bb9l5qq9papd5aqH3:')
            except:
                main_post_div = driver.find_element(By.XPATH, '//div[contains(@class, "xqtp20y") and contains(@class, "x6ikm8r") and contains(@class, "x10wlt62") and contains(@class, "x1n2onr6")]')

            # Locate all img elements within the main post div that contain 'scontent' in src attribute
            photo_elements = main_post_div.find_elements(By.XPATH, './/img[contains(@src, "scontent")]')
            
            # Extract the src attribute from each img element
            photo_links = [photo.get_attribute('src') for photo in photo_elements]

            # Assign the photo_links to post_data['photos']
            post_data['photos'] = photo_links

            # Print the links for verification
            for idx, link in enumerate(photo_links):
                print(f"Photo {idx + 1} link: {link}")

        except NoSuchElementException as e:
            print("No Element Photo")
            # Handle case where main post div is not found
            continue
        except Exception as e:
            print(e)
            # Handle any other exceptions
            continue
        # Extract reaction counts (this can vary based on the HTML structure)
        
        try:
            caption_element = driver.find_element(By.XPATH, '//div[@data-ad-comet-preview="message"]')
            caption = caption_element.text if caption_element else "No caption"
            
        except Exception as e:
            try:
                caption_element = driver.find_element(By.XPATH, '//div[contains(@class, "xdj266r") and contains(@class, "x11i5rnm") and contains(@class, "xat24cr") and contains(@class, "x1mh8g0r") and contains(@class, "x1vvkbs") and contains(@class, "x126k92a")]')
                caption = caption_element.text
            except Exception as e:
                caption = "No caption"
        post_data['caption'] = str(caption)   

        if caption == "No caption":
            print("Error caption")
            continue

        try:
            # Locate the element that needs to be hovered over to reveal the date
            date_element = driver.find_element(By.XPATH, '//span[contains(@class, "x1rg5ohu") and contains(@class, "x6ikm8r") and contains(@class, "x10wlt62") and contains(@class, "x16dsc37") and contains(@class, "xt0b8zv")]')

            # Perform a hover action on the date element
            ActionChains(driver).move_to_element(date_element).perform()

            
            # Wait for the tooltip or hover text to appear
            tooltip_element = WebDriverWait(driver, 25).until(EC.visibility_of_element_located((By.XPATH, '//div[@role="tooltip"]')))
    
            # Extract the text from the tooltip or hover text
            date_time_text = tooltip_element.text
            
            day_of_week, date_text = split_at_first_space(date_time_text)
            # Parse the date and time from the extracted text
            
            try:
                post_datetime = parse_facebook_date(date_text)
            except ValueError:
                # Handle relative times (e.g., "3 hours ago")
                post_datetime = datetime.now()
            
            publish_time = post_datetime.strftime('%H:%M:%S')
            publish_date = post_datetime.strftime('%Y-%m-%d')
            publish_day_of_week = post_datetime.strftime('%A')
            post_data['publish_time'] = post_datetime.strftime('%H:%M:%S')
            post_data['publish_date'] = post_datetime.strftime('%Y-%m-%d')
            post_data['publish_day_of_week'] = post_datetime.strftime('%A')
        except Exception as e:
            print(f"Error extracting date info for post {i}: {e}")
            continue
        # Extract specific reaction counts
        try:
            reaction_details = driver.find_elements(By.XPATH, '/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[1]/div/div/div/div/div/div/div/div/div/div/div/div/div/div[13]/div/div/div[4]/div/div/div[1]/div/div[1]/div/div[1]/div/span/div/span[2]/span/span')
            reactions = reaction_details[0].text
            print("Reaction number " + str(reactions))
            post_data['reactions'] = int(reaction_count(reactions))
        except Exception as e:
            print(f"Error extracting reaction details for post {i}: {e}")
            reactions = "No reactions found"
            post_data['reactions'] = 0
            
        
        try:
            share_element = driver.find_element(By.XPATH, '/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[1]/div/div/div/div/div/div/div/div/div/div/div/div/div/div[13]/div/div/div[4]/div/div/div[1]/div/div[1]/div/div[2]/div[3]/span/div')
            print("FOUND SHARE")
            share_text = share_element.text 
            print("Here is the share text" + str(share_text))
            share_count = parse_share_count(share_text)
            
            print(share_count)
            post_data['shares'] = int(share_count)
        except Exception as e:
            share_count = 0
            print("NOT FOUND SHARE")
            print(share_count)
            post_data['shares'] = 0
        try:
            comments = driver.find_element(By.XPATH, '/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[1]/div/div/div/div/div/div/div/div/div/div/div/div/div/div[13]/div/div/div[4]/div/div/div[1]/div/div[1]/div/div[2]/div[2]/span')
            comment_count = comments.text
            comment_count = parse_share_count(comment_count)
            print("Comment count")
            print(comment_count)
            post_data['comment_count'] = comment_count
            
        except Exception as e:
            comment_count = 0
            print("Comment count error")
            print(comment_count)
            post_data['comment_count'] = 0


        
        
        try:
            comment_list = []
            showcomment = driver.find_element(By.XPATH,'/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[1]/div[1]/div/div/div/div/div/div/div/div/div/div/div/div/div/div[13]/div/div/div[4]/div/div/div[2]/div[2]/div/div/span')
            showcomment.click()
            all_comment = driver.find_element(By.XPATH,'/html/body/div[1]/div/div[1]/div/div[3]/div/div/div[2]/div/div/div[1]/div[1]/div/div/div/div/div/div/div[1]/div/div[3]')
            all_comment.click()
            time.sleep(3)
            available_comment = driver.find_elements(By.XPATH, '//div[starts-with(@aria-label, "Comment by")]')
            for index, comment_element in enumerate(available_comment):

                try:
                    # Within each comment element, find the nested div containing the comment text
                    comment_text_element = comment_element.find_element(By.XPATH, './/div[contains(@class, "x1lliihq") and contains(@class, "xjkvuk6") and contains(@class, "x1iorvi4")]')
                    comment_text = comment_text_element.text.strip()
                    comment_list.append(str(comment_text))
                    
                    # Print the comment text
                    print(f"Comment {index + 1}: {comment_text}")
                    if index >= 10:
                        break

                except Exception as e:
                    # Skip the comment if an error occurs (likely "only-sticker" comments)
                    print(f"Skipping comment {index + 1} due to error: {e}")
                    if index >= 10:
                        break
                    continue
            
            
        except Exception as e:
            print("No comment")
        post_data['comment_details'] = comment_list
        


        print(f'Post {i}:')
        print(f'Link: {post_link}')
        print(f'Caption: {caption}')
        print(f'Reactions: {reactions}')
        print(f'Publish Time: {publish_time}')
        print(f'Publish Date: {publish_date}')
        print(f'Publish Day of Week: {publish_day_of_week}')
        print('---')
        print(post_data)
        print('---')
        
        data.append(post_data)

    return data


## Import extracted data into csv file

In [106]:
import csv
import os

header = ['post_id', 'page_name', 'page_follow', 'publish_date', 'publish_time', 'publish_day_of_week','shares', 'comment_count', 'caption', 'reactions', 'photos',  'comment_details']

# Check if the file exists
file_exists = os.path.isfile('final_facebook.csv')

def add_page_data(page_data, page_name, page_follow):
    
    with open('final_facebook.csv', 'a', newline='', encoding='utf-8') as csvfile:
        writer = csv.DictWriter(csvfile, fieldnames=header)
        # Write header only if the file is newly created
        if file_exists == False:
            writer.writeheader()
        for post in page_data:
            post['page_follow'] =   page_follow
            post['page_name'] = page_name  # Placeholder for the page name, to be filled later
            post['photos'] = ', '.join(post['photos'])  # Convert list of photos to a string
            post['comment_details'] = ', '.join(post['comment_details'])  # Convert list of comments to a string
            writer.writerow(post)

In [107]:
print(file_exists)

True


In [110]:

with open('final_facebook.csv', 'a', newline='', encoding='utf-8') as csvfile:
    writer = csv.DictWriter(csvfile, fieldnames=header)
        # Write header only if the file is newly created
    if file_exists == False:
        writer.writeheader()
    for post in infor_list[0]:
        post['page_follow'] =   49000
        post['page_name'] = 'FTU Corner'  # Placeholder for the page name, to be filled later
        post['photos'] = ', '.join(post['photos'])  # Convert list of photos to a string
        post['comment_details'] = ', '.join(post['comment_details'])  # Convert list of comments to a string
        writer.writerow(post)

In [117]:
def split_links(concatenated_links):
    # Initialize the list to hold individual links
    links = []
    start_idx = 0

    # Iterate through the string to find occurrences of 'http'
    while True:
        # Find the next occurrence of 'http' starting from the last found position
        next_idx = concatenated_links.find('http', start_idx + 4)
        if next_idx == -1:
            # If no more 'http' is found, append the remaining part of the string
            links.append(concatenated_links[start_idx:])
            break
        # Append the substring from the current start position to the position before the next 'http'
        links.append(concatenated_links[start_idx:next_idx])
        # Update the start position to the current 'http' found
        start_idx = next_idx

    return links

print(split_links('https://scontent.fhan5-9.fna.fbcdn.net/v/t39.30808-6/439054394_775527007889713_2231864830068118353_n.jpg?stp=dst-jpg_p526x395&_nc_cat=110&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeH94yyZ0grjVot0qfZ_-y7ATO68_mZt8PhM7rz-Zm3w-E_1edtmmRkxR-V9YR6nTKERhK5mSFVVk_Tdrj-GjOf3&_nc_ohc=lU_EuZ4_xH0Q7kNvgGuFGj6&_nc_ht=scontent.fhan5-9.fna&oh=00_AYDb9Fvss1EibJhpFJYT_7LJ0qbjEFx3BwVjU0Ih7zZrQg&oe=66765F9Bhttps://scontent.fhan5-8.fna.fbcdn.net/v/t39.30808-6/439462817_775527027889711_6179687775032595404_n.jpg?stp=dst-jpg_p526x395&_nc_cat=106&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeGftMXVii-QJBjdFTian2FG625exGZQbZXrbl7EZlBtlbglp2YWhMBZf6OFDqFt1cfMYd01HN1KeKMJe0_1ZKCR&_nc_ohc=T9dvhuzVakgQ7kNvgGl3oto&_nc_ht=scontent.fhan5-8.fna&oh=00_AYDyHehoG8xBzi_dEOMgmarKYrfE6_bI1ywDvjge6ttTjQ&oe=66763484https://scontent.fhan5-9.fna.fbcdn.net/v/t39.30808-6/439018226_775526994556381_7930470963539099358_n.jpg?stp=dst-jpg_p526x395&_nc_cat=110&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeHwrSnBnf9dCDrg5ThSiLYKPa4JSSSmKOA9rglJJKYo4FdO-91SmquE3ALCvf5TqIXDRR47Y78qBzZjvITz3svK&_nc_ohc=heKjruWOS9YQ7kNvgG10npr&_nc_ht=scontent.fhan5-9.fna&oh=00_AYBM13MQj0x-dBvkEinj1JhTgOSfyy10hjInHsyfVRnEjg&oe=66764812https://scontent.fhan5-11.fna.fbcdn.net/v/t39.30808-6/439343881_775526961223051_9073070978060726831_n.jpg?stp=dst-jpg_p526x395&_nc_cat=103&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeGdXIHGv8g8D9vFyYg_TDBnc6OShWfwdZ5zo5KFZ_B1nu1bddttRNNbop9WFGeb3B-N0VnedkkVWNlMAusdZ8yF&_nc_ohc=tXurTuc5cMYQ7kNvgGu73HL&_nc_ht=scontent.fhan5-11.fna&oh=00_AYAZX4Csku1HXByj2Ls5GvWP6eJsHPz5gVSTeJPAjijtHw&oe=66763A16https://scontent.fhan5-6.fna.fbcdn.net/v/t39.30808-6/439451851_775526971223050_2742212362298365240_n.jpg?stp=dst-jpg_p526x395&_nc_cat=105&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeECniv5HxCzfTNx3onAzwQ2VW312eT8q4JVbfXZ5Pyrgsfk-euQ5mrfX-SKtYbgzNk3B51e8DLsAoS67i4LIoBl&_nc_ohc=uMFfC6JlrtMQ7kNvgFjmEDG&_nc_ht=scontent.fhan5-6.fna&oh=00_AYCSwY4PxY87laO1al3W80nSwVD-boCR_0Sl9Gg7qB3S5w&oe=66763ADF'
))

['https://scontent.fhan5-9.fna.fbcdn.net/v/t39.30808-6/439054394_775527007889713_2231864830068118353_n.jpg?stp=dst-jpg_p526x395&_nc_cat=110&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeH94yyZ0grjVot0qfZ_-y7ATO68_mZt8PhM7rz-Zm3w-E_1edtmmRkxR-V9YR6nTKERhK5mSFVVk_Tdrj-GjOf3&_nc_ohc=lU_EuZ4_xH0Q7kNvgGuFGj6&_nc_ht=scontent.fhan5-9.fna&oh=00_AYDb9Fvss1EibJhpFJYT_7LJ0qbjEFx3BwVjU0Ih7zZrQg&oe=66765F9B', 'https://scontent.fhan5-8.fna.fbcdn.net/v/t39.30808-6/439462817_775527027889711_6179687775032595404_n.jpg?stp=dst-jpg_p526x395&_nc_cat=106&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeGftMXVii-QJBjdFTian2FG625exGZQbZXrbl7EZlBtlbglp2YWhMBZf6OFDqFt1cfMYd01HN1KeKMJe0_1ZKCR&_nc_ohc=T9dvhuzVakgQ7kNvgGl3oto&_nc_ht=scontent.fhan5-8.fna&oh=00_AYDyHehoG8xBzi_dEOMgmarKYrfE6_bI1ywDvjge6ttTjQ&oe=66763484', 'https://scontent.fhan5-9.fna.fbcdn.net/v/t39.30808-6/439018226_775526994556381_7930470963539099358_n.jpg?stp=dst-jpg_p526x395&_nc_cat=110&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeHwrSnBnf9dCDrg5ThSiLYKPa4JSSSmKOA9rglJJKYo4FdO-91Smq

In [130]:
page_followers = [
        ['https://www.facebook.com/schannel.vn/', 489000, "Schannel"],
    ["https://www.facebook.com/phephim/", 285000, "Phe Phim"],
    ["https://www.facebook.com/ScholarshipforVietnameseStudents/", 441000, "ScholarshipforVietnameseStudents"],
    ["https://www.facebook.com/vungvavap/", 44000, "Vung"],
    ["https://www.facebook.com/Codongpage/", 358000, "Co Dong"],
    ["https://www.facebook.com/marketinghive.dm/", 14000, "Marketing Hive"],
    ["https://www.facebook.com/vinuniharmony/", 2800, "VinUni Harmony"],
    ["https://www.facebook.com/MTP.Fan/", 14000000, "MTP"],
    ["https://www.facebook.com/vinuniversity/", 203000, "vinuniversity"],
    ["https://www.facebook.com/chaubui.official/", 2200000, "Chau Bui"],
    ["https://www.facebook.com/tran.thanh.ne/", 18000000, "Tran Thanh"],
    ["https://www.facebook.com/K14vn/", 55000000, "Kenh14"],
    ["https://www.facebook.com/VBA.vn/", 735000, "VBA"],
    ["https://www.facebook.com/Britishuniversityvietnam/", 127000, "BUV"],
    ["https://www.facebook.com/VinFastAuto.Official/", 668000, "Vinfast"],
    ["https://www.facebook.com/Theanh28/",9500000,"The Anh 28"],
    ["https://www.facebook.com/beatvn.network/", 2200000, "BeatVN"],
    ["https://www.facebook.com/elab.vinuni/", 685, "Elab VinUni"],
    ["https://www.facebook.com/ktqdNEU/", 385000, "NEU"],
    ["https://www.facebook.com/antiantiartprod/", 64000, "Anti Anti Art"],
    ["https://www.facebook.com/youthmedia.neu/", 31000, "Youth Media NEU"],
    ["https://www.facebook.com/tram.cotdien/", 167000, "Trạm"],
    ["https://www.facebook.com/mono.hng/", 387000, "MONO"],
    ["https://facebook.com/HIEUTHUHAIOFFICIAL/", 1400000, "HieuThuHai"],
    ["https://www.facebook.com/spacejump.official/", 33000, "Space Jump"],
    ["https://www.facebook.com/vinai.io/", 24000, "Vin AI Research"],
    ["https://www.facebook.com/BilliardsExpressVN/", 3300, "Billard VN"],
    ["https://www.facebook.com/daiphatthanh.sound/", 2200000, "Đài Phát Thanh"],
    ["https://www.facebook.com/ophimhayx/", 789000, "Ổ Phim"],
    ["https://www.facebook.com/InsightGenZvn/", 718000, "Insight Gen Z"],
    ["https://www.facebook.com/onestvn.media/", 142000, "Onest"],
    ["https://www.facebook.com/FTUSTUDENTOFFICIAL/", 49000, "FTU Corner"],
    ["https://www.facebook.com/TuyenVanHoaOfficial/", 3300000, "Tuyền Văn Hoá"],
    ["https://www.facebook.com/thethao247.vn/", 1400000, "Thể Thao 247"]


]

#end_id = data_of_post[-1]['post_id']
end_id = 0
data_list = []

for page in page_followers:
    permalink = get_post_link(page[0])
    data_post = extract_post_data(permalink,end_id)
    
    end_id += data_post[-1]['post_id']
    add_page_data(data_post,page[2],page[1])





1
Photo 1 link: https://scontent.fhan5-10.fna.fbcdn.net/v/t39.30808-6/430177861_747944880647926_3711744204970629926_n.jpg?stp=dst-jpg_s600x600&_nc_cat=111&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeFQRW2Q-UAf2NSDCp4ejNKiKD95hrL6_KYoP3mGsvr8pop4hLSPyV7EscdWahRESFzYjZ_Se3sMDHCVGgMy6Fey&_nc_ohc=0Ei6pGlWFGYQ7kNvgGhE2-l&_nc_ht=scontent.fhan5-10.fna&oh=00_AYA2G-eokdWUWCKoZslDWvWqBVjk7MttSp5SSXkXYL_e_w&oe=66769061
Photo 2 link: https://scontent.fhan5-11.fna.fbcdn.net/v/t39.30808-6/429973068_747944877314593_2785407384279789114_n.jpg?stp=dst-jpg_s600x600&_nc_cat=103&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeG2mP6ghCbFZmsqmxqrOWjOu8oafyba-667yhp_Jtr7rgicgp-rYR1dCiePFYfO1M3-dRXO2ZzCNryNXfjCTcKp&_nc_ohc=MyMMg9gYIngQ7kNvgHr_n3l&_nc_ht=scontent.fhan5-11.fna&oh=00_AYAJbhNIrZaMrhZSYA-G-zXDzmkSbLj9Cxbx1R3dkmmjKg&oe=667685D8
Reaction number 190
FOUND SHARE
Here is the share text37 shares
37
Comment count
7
Comment 1: Cơ hội ngon lành!
Comment 2: TN Tran Minh
Comment 3: Chou Chou
Comment 4: Vũ Phương Thảo ô =)))
Comment 

'  \n\ninfor_list  = []\nfor page in page_followers:\n    data_post = extract_post_data(link,end_id)\n    infor_list.append(data_post)\n    \n    add_page_data(data_post,page[2],page[1])\n    end_id += data_post[-1][\'post_id\']\n    print("-------------------------------PageExtractDone---------------------------")\n    print(page[2])\n'

## Download images based on their scontent links

In [158]:
import os
import pandas as pd
import requests
from urllib.parse import urlparse
from pathlib import Path

# Function to download and save image
def download_image(url, folder_path, filename):
    print(url)
    response = requests.get(url)
    if response.status_code == 200:
        with open(os.path.join(folder_path, filename), 'wb') as f:
            f.write(response.content)
            print(f"Downloaded: {filename}")

    else:
        print(f"Failed to download: {filename}")

# Function to process each row in the dataframe
def process_row(row, output_folder):

    post_id = row['post_id']
    photo_urls = row['photos'].split(", ")
    
    # Skip if photo_urls is empty
    if photo_urls[0] == 'nan':
        print(f"Skipping post {post_id} as no photos found.")
        return
    print(len(photo_urls))
    # Create directory if it doesn't exist
    output_folder_path = Path(output_folder)
    output_folder_path.mkdir(parents=True, exist_ok=True)
    
    # Download each photo
    for idx, photo_url in enumerate(photo_urls, start=1):
        print(photo_url)
        parsed_url = urlparse(photo_url)
        _, ext = os.path.splitext(parsed_url.path)
        filename = f"{post_id}-{idx}{ext}" if len(photo_urls) > 1 else f"{post_id}{ext}"
        download_image(photo_url, output_folder_path, filename)

# Path to your CSV file
csv_file = 'final_facebook.csv'

# Read CSV into pandas dataframe
df = pd.read_csv(csv_file)
df = df.dropna(subset=['photos'])
# Specify output folder to save images
output_folder = 'new_fb_images'

# Iterate over each row and process
for index, row in df.iterrows():
    process_row(row, output_folder)

1
https://scontent.fhan5-2.fna.fbcdn.net/v/t39.30808-6/448048755_1016327986726772_4700916560503043587_n.jpg?stp=dst-jpg_p526x296&_nc_cat=104&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeEhBIZ2E2AfkzbSe_icLhb6I7JKnR-sJP0jskqdH6wk_QxXwhZ4FK4lmmVj8OFmPzyTp6ePxxdivUtwY2qsSkvS&_nc_ohc=5OkhXy-ZeywQ7kNvgHYdc70&_nc_ht=scontent.fhan5-2.fna&oh=00_AYBsryfCFFUTOnAbOoi3Pq1-k3CzhLhcwd8srbRycfY0qA&oe=66745CDD
https://scontent.fhan5-2.fna.fbcdn.net/v/t39.30808-6/448048755_1016327986726772_4700916560503043587_n.jpg?stp=dst-jpg_p526x296&_nc_cat=104&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeEhBIZ2E2AfkzbSe_icLhb6I7JKnR-sJP0jskqdH6wk_QxXwhZ4FK4lmmVj8OFmPzyTp6ePxxdivUtwY2qsSkvS&_nc_ohc=5OkhXy-ZeywQ7kNvgHYdc70&_nc_ht=scontent.fhan5-2.fna&oh=00_AYBsryfCFFUTOnAbOoi3Pq1-k3CzhLhcwd8srbRycfY0qA&oe=66745CDD
Downloaded: 2.jpg
4
https://scontent.fhan5-11.fna.fbcdn.net/v/t39.30808-6/448268345_1016223386737232_1732088196342966091_n.jpg?stp=dst-jpg_p526x395&_nc_cat=103&ccb=1-7&_nc_sid=5f2048&_nc_eui2=AeEPLsZmYgG71e_h1Rer99MkSTV6WjglodtJ

## Calculate the sentiment score for posts

### 1. Create the react_ratio variable

In [151]:
import os
import pandas as pd
import requests
from urllib.parse import urlparse
from pathlib import Path

csv_file = 'final_facebook.csv'

# Read CSV into pandas dataframe
df = pd.read_csv(csv_file)
df = df.dropna(subset=['photos'])
df.head()
#df.shape

post_id page_name  page_follow publish_date publish_time  \
0        2  Schannel       489000    6/13/2024     16:21:00   
4        6  Schannel       489000    6/13/2024     11:28:00   
5        7  Schannel       489000    1/17/2024     11:37:00   
6        8  Schannel       489000    6/14/2024     19:12:00   
9       12  Schannel       489000   12/15/2023      8:50:00   

  publish_day_of_week  shares  comment_count  \
0            Thursday       1              6   
4            Thursday       0              4   
5           Wednesday       0             17   
6              Friday       2              3   
9              Friday       1              9   

                                             caption  reactions  \
0  Vào tối 12/6, hàng loạt người dùng trên mạng x...        849   
4  SCHANNEL TẠI CÔNG CHIẾU PHIM INSIDE OUT 2 \nXe...        288   
5  CẢNH BÁO: NHIỀU FANPAGE F.A.K.E\nGIẢ DANH SCHA...        373   
6  CHẤN ĐỘNG \n CELLPHONES ĐÃ CẬP BẾN NHA TRANG -...       1200   
9  [NHỜ BÁO CÁO LỪA ĐẢO]\nMột page giả mạo, sử dụ...        302   

                                              photos  \
0  https://scontent.fhan5-2.fna.fbcdn.net/v/t39.3...   
4  https://scontent.fhan5-11.fna.fbcdn.net/v/t39....   
5  https://scontent.fhan5-11.fna.fbcdn.net/v/t39....   
6  https://scontent.fhan5-9.fna.fbcdn.net/v/t39.3...   
9  https://scontent.fhan5-10.fna.fbcdn.net/v/t39....   

                                     comment_details  
0  Chú thợ hát nào đó từng nói ..., Lan Chi đừng ...  
4  Mai em mới đi xem nhưng mà mong chờ được card ...  
5  Linh này bạn :))), Mới đây lun, Mới đây nữa nà...  
6  Mọi người nhớ ghé qua số 3 Thái Nguyên vào ngà...  
9  Bài đăng giả mạo, mong cả nhà report giúp chún...

In [152]:
df['react_ratio'] = df['reactions'] / df['page_follow']*1000

### 2. Conduct sentiment analysis 

In [154]:
# Create the new 'comment_list' column by splitting 'comment_details' on commas
df['comment_list'] = df['comment_details'].apply(lambda x: x.split(',') if isinstance(x, str) else [])

# Ensure each entry in 'comment_list' is a list
df['comment_list'] = df['comment_list'].apply(lambda x: x if isinstance(x, list) else [])

# Verify that each element is a list
df.head()

post_id page_name  page_follow publish_date publish_time  \
0        2  Schannel       489000    6/13/2024     16:21:00   
4        6  Schannel       489000    6/13/2024     11:28:00   
5        7  Schannel       489000    1/17/2024     11:37:00   
6        8  Schannel       489000    6/14/2024     19:12:00   
9       12  Schannel       489000   12/15/2023      8:50:00   

  publish_day_of_week  shares  comment_count  \
0            Thursday       1              6   
4            Thursday       0              4   
5           Wednesday       0             17   
6              Friday       2              3   
9              Friday       1              9   

                                             caption  reactions  \
0  Vào tối 12/6, hàng loạt người dùng trên mạng x...        849   
4  SCHANNEL TẠI CÔNG CHIẾU PHIM INSIDE OUT 2 \nXe...        288   
5  CẢNH BÁO: NHIỀU FANPAGE F.A.K.E\nGIẢ DANH SCHA...        373   
6  CHẤN ĐỘNG \n CELLPHONES ĐÃ CẬP BẾN NHA TRANG -...       1200   
9  [NHỜ BÁO CÁO LỪA ĐẢO]\nMột page giả mạo, sử dụ...        302   

                                              photos  \
0  https://scontent.fhan5-2.fna.fbcdn.net/v/t39.3...   
4  https://scontent.fhan5-11.fna.fbcdn.net/v/t39....   
5  https://scontent.fhan5-11.fna.fbcdn.net/v/t39....   
6  https://scontent.fhan5-9.fna.fbcdn.net/v/t39.3...   
9  https://scontent.fhan5-10.fna.fbcdn.net/v/t39....   

                                     comment_details  react_ratio  \
0  Chú thợ hát nào đó từng nói ..., Lan Chi đừng ...     1.736196   
4  Mai em mới đi xem nhưng mà mong chờ được card ...     0.588957   
5  Linh này bạn :))), Mới đây lun, Mới đây nữa nà...     0.762781   
6  Mọi người nhớ ghé qua số 3 Thái Nguyên vào ngà...     2.453988   
9  Bài đăng giả mạo, mong cả nhà report giúp chún...     0.617587   

                                        comment_list  
0  [Chú thợ hát nào đó từng nói ...,  Lan Chi đừn...  
4  [Mai em mới đi xem nhưng mà mong chờ được card...  
5  [Linh này bạn :))),  Mới đây lun,  Mới đây nữa...  
6  [Mọi người nhớ ghé qua số 3 Thái Nguyên vào ng...  
9  [Bài đăng giả mạo,  mong cả nhà report giúp ch...

In [153]:
import re
import string
def clean_comment(comment):
    # Remove URLs
    comment = re.sub(r'http\S+', '', comment)
    
    # Remove punctuation and symbols
    comment = comment.translate(str.maketrans('', '', string.punctuation))
    
    # Remove additional patterns or symbols specific to your case
    # For example, removing mentions or hashtags
    
    return comment.strip()

In [155]:
# Create a Translator object
translator = Translator()
sia = SentimentIntensityAnalyzer()
for index, row in df.iterrows():
  if len(row['comment_list']) == 0:
    df.at[index, 'average_score'] = -1
  else:
    total = 0
    previous_score =0
    for comment in row['comment_list']:
      comment = clean_comment(comment)
      try:
        translation = translator.translate(str(comment), src='vi', dest='en')
        score = sia.polarity_scores(translation.text)['compound']
      except:
        score = previous_score
      total+= score
      previous_score = score
    average_score = total/len(row['comment_list'])
    df.at[index, 'average_score'] = average_score


Row process:1/1099
Row process:1/1099
Row process:1/1099
Row process:1/1099
Row process:1/1099
Row process:1/1099
Row process:2/1099
Row process:2/1099
Row process:2/1099
Row process:2/1099
Row process:3/1099
Row process:3/1099
Row process:3/1099
Row process:3/1099
Row process:3/1099
Row process:3/1099
Row process:3/1099
Row process:3/1099
Row process:4/1099
Row process:4/1099
Row process:4/1099
Row process:4/1099
Row process:4/1099
Row process:5/1099
Row process:5/1099
Row process:5/1099
Row process:5/1099
Row process:5/1099
Row process:5/1099
Row process:5/1099
Row process:5/1099
Row process:5/1099
Row process:5/1099
Row process:5/1099
Row process:6/1099
Row process:6/1099
Row process:6/1099
Row process:6/1099
Row process:6/1099
Row process:6/1099
Row process:6/1099
Row process:6/1099
Row process:6/1099
Row process:6/1099
Row process:6/1099
Row process:7/1099
Row process:7/1099
Row process:7/1099
Row process:7/1099
Row process:7/1099
Row process:7/1099
Row process:7/1099
Row process:

In [6]:
import pandas as pd
import numpy as np
import os
import cv2
import tensorflow as tf
from sklearn.model_selection import train_test_split
from tensorflow.keras import layers, models, callbacks
from tqdm import tqdm




## Pre Process Images for the case of multiple images/post

In [159]:
import os
from PIL import Image
import pandas as pd



# Directory containing the images
image_dir = 'new_fb_images'

# Directory to save composite images
output_dir = 'composite_images'
os.makedirs(output_dir, exist_ok=True)


def crop_center(img, crop_width, crop_height):
    img_width, img_height = img.size
    return img.crop((
        (img_width - crop_width) // 2,
        (img_height - crop_height) // 2,
        (img_width + crop_width) // 2,
        (img_height + crop_height) // 2
    ))

def concatenate_images(image_paths, output_path):
    images = [Image.open(image_path) for image_path in image_paths]
    
    # Find the smallest width and height among the images
    min_width = min(img.width for img in images)
    min_height = min(img.height for img in images)

    if len(images) == 1:
        # Just save the single image with the post ID as filename
        images[0].save(output_path)
    else:
        # Crop images to the smallest width and height
        cropped_images = [crop_center(img, min_width, min_height) for img in images]

        if len(cropped_images) == 2:
            # Horizontally concatenate
            total_width = sum(img.width for img in cropped_images)
            max_height = max(img.height for img in cropped_images)
            composite_image = Image.new('RGB', (total_width, max_height))
            x_offset = 0
            for img in cropped_images:
                composite_image.paste(img, (x_offset, 0))
                x_offset += img.width

        elif len(cropped_images) == 3:
            total_width = sum(img.width for img in cropped_images)
            max_height = max(img.height for img in cropped_images)

            # Create a new blank image with the total width and max height
            composite_image = Image.new('RGB', (total_width, max_height))

            x_offset = 0
            for img in cropped_images:
                composite_image.paste(img, (x_offset, 0))
                x_offset += img.width

        elif len(cropped_images) == 4:
            # Arrange in a 2x2 grid
            total_width = 2 * min_width
            total_height = 2 * min_height
            composite_image = Image.new('RGB', (total_width, total_height))
            x_offset = 0
            y_offset = 0
            for i, img in enumerate(cropped_images):
                composite_image.paste(img, (x_offset, y_offset))
                x_offset += img.width
                if (i + 1) % 2 == 0:
                    x_offset = 0
                    y_offset += img.height

        elif len(cropped_images) == 5:
            # Arrange in a 2x2 grid for the first four, and concatenate the fifth image below with double width
            total_width = 2 * min_width
            total_height = 3 * min_height
            composite_image = Image.new('RGB', (total_width, total_height))
            x_offset = 0
            y_offset = 0
            for i, img in enumerate(cropped_images[:4]):
                composite_image.paste(img, (x_offset, y_offset))
                x_offset += img.width
                if (i + 1) % 2 == 0:
                    x_offset = 0
                    y_offset += img.height

            # Crop the fifth image to center and double its width
            fifth_img = cropped_images[4]
            double_width = 2 * fifth_img.width
            fifth_img_cropped = crop_center(fifth_img, double_width, fifth_img.height)
            composite_image.paste(fifth_img_cropped, (0, 2 * min_height))

        else:
            # If more than 5 images, you can customize as needed
            raise NotImplementedError("Concatenation for more than 5 images not implemented.")

        # Save the composite image with the correct filename
        composite_image.save(output_path)

# Process images in the folder
for root, _, files in os.walk(image_dir):
    post_images = {}
    for file in files:
        if file.endswith('.jpg'):
            post_id = file.split('-')[0]
            if post_id not in post_images:
                post_images[post_id] = []
            post_images[post_id].append(os.path.join(root, file))
    print(post_images)
    for post_id, image_paths in post_images.items():
        # Concatenate and save the composite image
        if 'jpg' not in post_id:
            output_path = os.path.join(output_dir, f"{post_id}.jpg")
        else:
            output_path = os.path.join(output_dir, post_id)
        concatenate_images(image_paths, output_path)


{'100.jpg': ['new_fb_images\\100.jpg'], '1003321959.jpg': ['new_fb_images\\1003321959.jpg'], '1003321960.jpg': ['new_fb_images\\1003321960.jpg'], '1003321962.jpg': ['new_fb_images\\1003321962.jpg'], '1003321965.jpg': ['new_fb_images\\1003321965.jpg'], '1003321966.jpg': ['new_fb_images\\1003321966.jpg'], '1003321969.jpg': ['new_fb_images\\1003321969.jpg'], '1003321970.jpg': ['new_fb_images\\1003321970.jpg'], '1003321973.jpg': ['new_fb_images\\1003321973.jpg'], '1003321974.jpg': ['new_fb_images\\1003321974.jpg'], '1003321975.jpg': ['new_fb_images\\1003321975.jpg'], '1003321977.jpg': ['new_fb_images\\1003321977.jpg'], '1003321978.jpg': ['new_fb_images\\1003321978.jpg'], '1003321980.jpg': ['new_fb_images\\1003321980.jpg'], '1003321981.jpg': ['new_fb_images\\1003321981.jpg'], '1003321982': ['new_fb_images\\1003321982-1.jpg', 'new_fb_images\\1003321982-2.jpg', 'new_fb_images\\1003321982-3.jpg'], '1003321983': ['new_fb_images\\1003321983-1.jpg', 'new_fb_images\\1003321983-2.jpg'], '1003321984

In [45]:


# Function to load and preprocess images
def load_and_preprocess_images(df, image_folder):
    image_data = []
    for index, row in tqdm(df.iterrows(), desc="Loading Images", total=len(df)):
        post_id = row['post_id']


        image_path = os.path.join(image_folder, f"{post_id}.jpg")

        
        
        if os.path.exists(image_path):
            image = cv2.imread(image_path)
            image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)  # Convert BGR to RGB
            image = cv2.resize(image, (224, 224))  # Resize image to 224x224
            image = image.astype(np.float32) / 255.0  # Normalize pixel values
            image_data.append(image)
        else: 
            print("Not found")
    return np.array(image_data)

# Example usage

image_folder = 'D:\Spring24\Data Mining\Project\composite_images'



# Load and preprocess images
X_images = load_and_preprocess_images(df, image_folder)

Loading Images: 100%|██████████| 322/322 [00:02<00:00, 124.27it/s]
